# ZERO SHOT PROMPT


In [1]:
import os
import json
import numpy
import subprocess


def generate_cot_dataset(json_path="../training_data/train.json", output_path="llama-2-train.json"):
    data_zip_path = "../training_data.zip"
    data_path = "../training_data"
    if not os.path.exists(data_path):
        unzip_cmd = f"unzip {data_zip_path}"
        subprocess.run(unzip_cmd, shell=True)

    CT_json_dir = os.path.join(data_path, "CT json")
    with open(json_path) as json_file:
        subdata_set = json.load(json_file)
    
    subdata_uuid_list = list(subdata_set.keys())
    # print(subdata_uuid_list)
    subdata_statements = [subdata_set[subdata_uuid_list[i]]["Statement"] for i in range(len(subdata_uuid_list))]
    subdata_json_list = []
    for i in range(len(subdata_uuid_list)):
        datapoint = subdata_set[subdata_uuid_list[i]]
        primary_ctr_path = os.path.join(CT_json_dir, datapoint["Primary_id"]+".json")
        with open(primary_ctr_path) as json_file:
            primary_ctr = json.load(json_file)
        
        sys_prompt = f"For this task You are going to determine the inference relation (entailment or contradiction) between pairs of Clinical Trial Reports (CTRs) and the statements, making claims about one of the summarized sections of the CTRs: {datapoint['Section_id']}."
        input_prompt = [f"This task type is \"{datapoint['Type']}\"."]
        if datapoint["Type"] == "Comparison":
            input_prompt += ["There are multiple CTRs."]
        # else:
        #     input_prompt += ["There is only one CTR."]

        #Retrieve the full section from the primary trial
        primary_section = primary_ctr[datapoint["Section_id"]]

        statement = subdata_statements[i]
        input_prompt += [f"The statement is \"{statement}\"."]
        input_prompt += [f"The primary CTR section includes,\n"]
        input_prompt += [''.join(primary_section)]
        #Repeat for the secondary trial
        if datapoint["Type"] == "Comparison":
            secondary_ctr_path = os.path.join(CT_json_dir, datapoint["Secondary_id"]+".json")
            with open(secondary_ctr_path) as json_file:
                secondary_ctr = json.load(json_file)
            secondary_section = secondary_ctr[datapoint["Section_id"]]

            input_prompt += [f"The secondary CTR section includes,"]
            input_prompt += ['\n'.join(secondary_section)]

        output_prompt = [".Just answer in one word either entailment or contradiction "]
        # output_prompt += ["I found the evidence in those lines are important, \nPrimary_evidence_index: " + str(datapoint["Primary_evidence_index"])]
        # if datapoint["Type"] == "Comparison":
        #     output_prompt += ["Secondary_evidence_index: " + str(datapoint["Secondary_evidence_index"])]
        # output_prompt += [f"what do you think the relationship is, think step by step."]

        # output_prompt += [f"what do you think the relationship is \"{datapoint['Label']}\"."]
        input_prompt, output_prompt = ' '.join(input_prompt), ' '.join(output_prompt)
        subdata_json_list.append({
            "text": f"{sys_prompt}. {input_prompt} {output_prompt}"
        })

    print(subdata_json_list)
    with open(output_path, 'w') as jsonFile:
        jsonFile.write(json.dumps(subdata_json_list, indent=4))


if __name__ == '__main__':
    generate_cot_dataset(json_path="../training_data/train.json", output_path="zero_prompt-2-train.json")
    generate_cot_dataset(json_path="../training_data/dev.json", output_path="zer0_prompt-2-dev.json")
# generate_cot_dataset

[{'text': 'For this task You are going to determine the inference relation (entailment or contradiction) between pairs of Clinical Trial Reports (CTRs) and the statements, making claims about one of the summarized sections of the CTRs: Intervention.. This task type is "Comparison". There are multiple CTRs. The statement is "All the primary trial participants do not receive any oral capecitabine, oral lapatinib ditosylate or cixutumumab IV, in conrast all the secondary trial subjects receive these.". The primary CTR section includes,\n INTERVENTION 1:   Diagnostic (FLT PET)  Patients with early stage, ER positive primary breast cancer undergo FLT PET scan at baseline and 1-6 weeks after the start of standard endocrine treatment. The surgery follows 1-7 days after the second FLT PET scan.  Tracer used in the FLT PET (positron emission tomography) scanning procedure: [F18] fluorothymidine.  Positron Emission Tomography: Undergo FLT PET  Laboratory Biomarker Analysis: Correlative studies -

# COT PROMPT

In [2]:
import os
import json
import numpy
import subprocess


def generate_cot_dataset(json_path="../training_data/train.json", output_path="llama-2-train.json"):
    data_zip_path = "../training_data.zip"
    data_path = "../training_data"
    if not os.path.exists(data_path):
        unzip_cmd = f"unzip {data_zip_path}"
        subprocess.run(unzip_cmd, shell=True)

    CT_json_dir = os.path.join(data_path, "CT json")
    with open(json_path) as json_file:
        subdata_set = json.load(json_file)
    
    subdata_uuid_list = list(subdata_set.keys())
    # print(subdata_uuid_list)
    subdata_statements = [subdata_set[subdata_uuid_list[i]]["Statement"] for i in range(len(subdata_uuid_list))]
    subdata_json_list = []
    for i in range(len(subdata_uuid_list)):
        datapoint = subdata_set[subdata_uuid_list[i]]
        primary_ctr_path = os.path.join(CT_json_dir, datapoint["Primary_id"]+".json")
        with open(primary_ctr_path) as json_file:
            primary_ctr = json.load(json_file)
        
        sys_prompt = f"You are a helpful assistant, for this task, you have to think step by step, remember that. You are going to determine the inference relation (entailment or contradiction) between pairs of Clinical Trial Reports (CTRs) and the statements, making claims about one of the summarized sections of the CTRs: {datapoint['Section_id']}."
        input_prompt = [f"This task type is \"{datapoint['Type']}\"."]
        if datapoint["Type"] == "Comparison":
            input_prompt += ["There are multiple CTRs."]
        else:
            input_prompt += ["There is only one CTR."]

        #Retrieve the full section from the primary trial
        primary_section = primary_ctr[datapoint["Section_id"]]

        statement = subdata_statements[i]
        input_prompt += [f"The statement is \"{statement}\"."]
        input_prompt += [f"The primary CTR section includes,\n"]
        input_prompt += [''.join(primary_section)]
        #Repeat for the secondary trial
        if datapoint["Type"] == "Comparison":
            secondary_ctr_path = os.path.join(CT_json_dir, datapoint["Secondary_id"]+".json")
            with open(secondary_ctr_path) as json_file:
                secondary_ctr = json.load(json_file)
            secondary_section = secondary_ctr[datapoint["Section_id"]]

            input_prompt += [f"The secondary CTR section includes,"]
            input_prompt += ['\n'.join(secondary_section)]

        output_prompt = ["Based on the provided evidence, "]
        # output_prompt += ["I found the evidence in those lines are important, \nPrimary_evidence_index: " + str(datapoint["Primary_evidence_index"])]
        # if datapoint["Type"] == "Comparison":
        #     output_prompt += ["Secondary_evidence_index: " + str(datapoint["Secondary_evidence_index"])]
        output_prompt += [f"what do you think the relationship is, think step by step."]

        # output_prompt += [f"what do you think the relationship is \"{datapoint['Label']}\"."]
        input_prompt, output_prompt = ' '.join(input_prompt), ' '.join(output_prompt)
        subdata_json_list.append({
            "text": f"{sys_prompt}. {input_prompt} {output_prompt}"
        })

    print(subdata_json_list)
    with open(output_path, 'w') as jsonFile:
        jsonFile.write(json.dumps(subdata_json_list, indent=4))


if __name__ == '__main__':
    generate_cot_dataset(json_path="../training_data/train.json", output_path="prompt-2-train.json")
    generate_cot_dataset(json_path="../training_data/dev.json", output_path="prompt-2-dev.json")
# generate_cot_dataset

[{'text': 'You are a helpful assistant, for this task, you have to think step by step, remember that. You are going to determine the inference relation (entailment or contradiction) between pairs of Clinical Trial Reports (CTRs) and the statements, making claims about one of the summarized sections of the CTRs: Intervention.. This task type is "Comparison". There are multiple CTRs. The statement is "All the primary trial participants do not receive any oral capecitabine, oral lapatinib ditosylate or cixutumumab IV, in conrast all the secondary trial subjects receive these.". The primary CTR section includes,\n INTERVENTION 1:   Diagnostic (FLT PET)  Patients with early stage, ER positive primary breast cancer undergo FLT PET scan at baseline and 1-6 weeks after the start of standard endocrine treatment. The surgery follows 1-7 days after the second FLT PET scan.  Tracer used in the FLT PET (positron emission tomography) scanning procedure: [F18] fluorothymidine.  Positron Emission Tomo